In [7]:
import pandas as pd


FOR EACH CONDITION PERFORM THE NECESSARY OPERATION 

In [8]:
def handling_duplicates(df, i ,cleaned_list ) :

    dup = i.values['n_duplicates']
    df.drop_duplicates(inplace=True)                  # dropped from the original column
    
    cleaned_list.append(f" {dup} Duplicates rows are removed ")

In [9]:
def handling_zeros(df, i , cleaned_list) :
    
    zeron = i.values['n_zeros']      # telling the count only
    zerop = i.values['p_zeros']*100
    
    cleaned_list.append(f"{i.column_name} has {zerop}% zeros ")

In [10]:
def handling_missing(df,i,cleaned_list,alert_list) :

    null = i.values['p_missing']*100

    if null > 60 :
            df.drop(columns=[i.column_name],inplace=True )
            cleaned_list.append(f"The {i.column_name} is been dropped due to > 60% missing_values")
    
    else :
        # ifcoln_is numeric
        
            if alert_list.variables[i.column_name]['type'] == 'Numeric' :
                median_value = df[i.column_name].median()
        
                df[i.column_name].fillna(median_value ,inplace=True)
                cleaned_list.append(f"Missing values of {i.column_name}  has been imputed with value {median_value} ")

        # ifcoln_is object
        
            else :

                mode_val = df[i.column_name].mode()[0]
                df[i.column_name].fillna(mode_val ,inplace=True)
                
                cleaned_list.append(f"Imputed missing values of {i.column_name} with {mode_val} ")

        

In [11]:
df= pd.read_csv('titanic.csv')

In [12]:
df

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    male  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                               Heikkinen, Miss. Laina  female  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                             Allen, Mr. William Henry    male  35.0      0   
..                                                 ...     ...   ...    ...   
886                              Montvila, Rev. Juozas    male  27.0      0   
887                       Graham, Miss. Margaret Edith  female  19.0      0   
888           Johnston, Miss. Catherine Helen "Carrie"  female   NaN      1   
889                              Behr, Mr. Karl Howell    male  26.0      0   
890                                Dooley, Mr. Patrick    male  32.0      0   

     Parch            Ticket     Fare Cabin Embarked  
0        0         A/5 21171   7.2500   NaN        S  
1        0          PC 17599  71.2833   C85        C  
2        0  STON/O2. 3101282   7.9250   NaN        S  
3        0            113803  53.1000  C123        S  
4        0            373450   8.0500   NaN        S  
..     ...               ...      ...   ...      ...  
886      0            211536  13.0000   NaN        S  
887      0            112053  30.0000   B42        S  
888      2        W./C. 6607  23.4500   NaN        S  
889      0            111369  30.0000  C148        C  
890      0            370376   7.7500   NaN        Q  

[891 rows x 12 columns]

In [13]:
# EXTRACTING VALUABLE FEATURES FROM THE DF EARILER ONLY

CREATING COPY OF ORIGINAL DATA TO COMPARE WITH FINAL OUTPUT

In [14]:
df_copy = df.copy()
cleaned_list = []

CONVERTING THE POSSIBLE COLUMNS TO DATETIME FORMAT

In [15]:
for i in df.columns :

    #converting possible colns into (datetime) datatype
    coln_converted = pd.to_datetime(df[i] , errors='coerce')   # if notconv_then nan value
    
    # checking _% of not nullvalues
    non_null_values  = coln_converted.notna().sum() / len(coln_converted)
     
    if non_null_values > 0.6 :
        
        if coln_converted.dt.month.nunique() > 2 or coln_converted.dt.day.nunique() > 2  :      #(applied some uniqueness_logic)dt - pandas DatetimeIndex

            cleaned_list.append(f"Column {i} has been detected as Datetime Column")
    #for day
            df[f'{i}_year'] = coln_converted.dt.year             # .dt only works on a series that has_converted todatetime 
            df[f'{i}_month'] =  coln_converted.dt.month
            df[f'{i}_day'] =  coln_converted.dt.day
    #for time
            df[f'{i}_hours'] = coln_converted.dt.hour            # .dt only works on a series that has_converted todatetime 
            df[f'{i}_minute'] =  coln_converted.dt.minute
            df[f'{i}_second'] =  coln_converted.dt.second
 
            df.drop(columns=[i] , inplace=True)                # dropping the original coln
            
        else :

            df[i] = df_copy[i]
            

C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2695674617.py:4: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  coln_converted = pd.to_datetime(df[i] , errors='coerce')   # if notconv_then nan value
C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2695674617.py:4: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  coln_converted = pd.to_datetime(df[i] , errors='coerce')   # if notconv_then nan value
C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2695674617.py:4: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  coln_converted = pd.to_datetime(df[i] , errors='coerce')   # if not

CONVERTING POSSIBLE APLHANUMERIC STRINGS TO SEPERATE COLUMNS

In [16]:
for i in df.columns :

        if df[i].dtype == 'object':           # always in the part of object datatype
            
            # Specific logic for Ticket and cabin like columns
            type_ticket = r'^.*?[\s]*\d+$'
            
            type_cabin = r'^[A-Z]\d+'

            coln_sample = df[i].dropna().sample(n = min(100,len(df[i].dropna())), random_state=1 )  # savingthe runtime

            # then string matching percentage of columns                         using str.match()
            
            ticket_percentage = coln_sample.str.match(type_ticket).mean()
            cabin_percentage = coln_sample.str.match(type_cabin).mean()

            if ticket_percentage > 0.6 :

                col_as_str = df[i].astype(str)
                df[f'{i}_prefix'] = col_as_str.str.replace(r'\s*\d+$', '', regex=True).str.strip()
                df[f'{i}_prefix'].replace('', 'NONE', inplace=True)
                df[f'{i}_number'] = pd.to_numeric(col_as_str.str.extract(r'(\d+)$')[0], errors='coerce')
                
                df.drop(columns=[i], inplace=True)
                cleaned_list.append(f"SUCCESS: Split '{i}' into prefix/number and dropped original.")

            
            # Specific logic for Cabin-like columns
            elif cabin_percentage > 0.6 :
                
                col_as_str = df[col_name].str.extract(r'^([A-Z])(\d+.*)', expand=True)
                df[f'{i}_prefix'] = col_as_str.str[0]
                df[f'{i}_number'] = pd.to_numeric(col_as_str[1], errors='coerce')
                df.drop(columns=[i], inplace=True)
                cleaned_list.append(f"SUCCESS: Created '{i}_prefix' from '{i}' and dropped original.")



C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2054746293.py:21: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df[f'{i}_prefix'].replace('', 'NONE', inplace=True)
C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2054746293.py:21: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

Fo

USING THE PYTHON'S INBUILT LIBRARY - ProfileReport TO DIRECTLY ATTACK ON POTENTIAL FLAW OF DATASET

In [17]:
from ydata_profiling import ProfileReport
 
# creating object of ProfileReport

fd =  ProfileReport(df)


In [18]:
# get_description in dictionary format (return full structured JSON format)

alert_list = fd.get_description()
alert_list

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 14/14 [00:00<00:00, 455.19it/s]


BaseDescription(analysis=BaseAnalysis(title='YData Profiling Report', date_start=datetime.datetime(2025, 9, 28, 18, 35, 38, 235204), date_end=datetime.datetime(2025, 9, 28, 18, 35, 51, 542546)), time_index_analysis=None, table={'n': 891, 'n_var': 14, 'memory_size': np.int64(99920), 'record_size': 112.14365881032548, 'n_cells_missing': np.int64(874), 'n_vars_with_missing': 4, 'n_vars_all_missing': 0, 'p_cells_missing': np.float64(0.0700657367324034), 'types': {'Numeric': 7, 'Categorical': 6, 'Text': 1}, 'n_duplicates': 0, 'p_duplicates': 0.0}, variables={'PassengerId': {'n_distinct': 891, 'p_distinct': 1.0, 'is_unique': True, 'n_unique': np.int64(891), 'p_unique': np.float64(1.0), 'type': 'Numeric', 'hashable': True, 'value_counts_without_nan': PassengerId
891    1
1      1
2      1
3      1
4      1
      ..
16     1
15     1
14     1
13     1
12     1
Name: count, Length: 891, dtype: int64, 'value_counts_index_sorted': PassengerId
1      1
2      1
3      1
4      1
5      1
      ..


In [19]:
from ydata_profiling.model.alerts import  AlertType       # to directly_work go the alert section

result = alert_list.alerts           # returns list
result

[[Cabin_prefix] is highly overall correlated with [Fare] and 1 other fields,
 [Fare] is highly overall correlated with [Cabin_prefix],
 [Pclass] is highly overall correlated with [Cabin_prefix],
 [Sex] is highly overall correlated with [Survived],
 [SibSp] is highly overall correlated with [Ticket_prefix],
 [Survived] is highly overall correlated with [Sex],
 [Ticket_number] is highly overall correlated with [Ticket_prefix],
 [Ticket_prefix] is highly overall correlated with [SibSp] and 1 other fields,
 [Ticket_prefix] is highly imbalanced (0.6449729473793234),
 [Cabin_prefix] is highly imbalanced (0.6533990117750507),
 [Age] 177 (19.9%) missing values,
 [Cabin_number] 691 (77.6%) missing values,
 [PassengerId] is uniformly distributed,
 [PassengerId] has unique values,
 [Name] has unique values,
 [SibSp] has 608 (68.2%) zeros,
 [Parch] has 678 (76.1%) zeros,
 [Fare] has 15 (1.7%) zeros]

CREATING SET TO SEPERATE OUT THE highly_correlated ONCE COLNS . SO THAT THE DATASET DONOT GET AFFECTED

In [20]:
high_cooreln = set()

for i in result :
    print(i.column_name , i.alert_type )

    if i.alert_type == AlertType.HIGH_CORRELATION :
        high_cooreln.add(i.column_name)


        
print (high_cooreln)

Cabin_prefix AlertType.HIGH_CORRELATION
Fare AlertType.HIGH_CORRELATION
Pclass AlertType.HIGH_CORRELATION
Sex AlertType.HIGH_CORRELATION
SibSp AlertType.HIGH_CORRELATION
Survived AlertType.HIGH_CORRELATION
Ticket_number AlertType.HIGH_CORRELATION
Ticket_prefix AlertType.HIGH_CORRELATION
Ticket_prefix AlertType.IMBALANCE
Cabin_prefix AlertType.IMBALANCE
Age AlertType.MISSING
Cabin_number AlertType.MISSING
PassengerId AlertType.UNIFORM
PassengerId AlertType.UNIQUE
Name AlertType.UNIQUE
SibSp AlertType.ZEROS
Parch AlertType.ZEROS
Fare AlertType.ZEROS
{'Survived', 'SibSp', 'Cabin_prefix', 'Ticket_prefix', 'Fare', 'Sex', 'Ticket_number', 'Pclass'}


MAIN ENGINE(STRUCTURE)

In [21]:
for i in result :
        
    
    if(i.alert_type ==  AlertType.DUPLICATES ) :

        if i.column_name in high_cooreln :
            cleaned_list.append(f"{i.column_name} duplicates columns are not removed due to high correlation .Manual Review Recommended")
            continue
            
        handling_duplicates(df, i ,cleaned_list)
        
    elif(i.alert_type == AlertType.ZEROS ) :
            
         handling_zeros(df, i, cleaned_list)
    
    elif(i.alert_type == AlertType.MISSING ) :

        if i.column_name in high_cooreln :
            cleaned_list.append(f"{i.column_name} not Imputed due to high correlation.Manual Review Recommended")
            continue
        
        handling_missing(df, i, cleaned_list , alert_list)
    
    elif i.alert_type == AlertType.UNIQUE :
        
        cleaned_list.append(f"{i.column_name} has 100% Unique values")

    elif i.alert_type ==  AlertType.HIGH_CARDINALITY :

        cleaned_list.append(f"{i.column_name} has HIGH_CARDINALITY")
        

C:\Users\impar\AppData\Local\Temp\ipykernel_20992\2189025671.py:15: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df[i.column_name].fillna(median_value ,inplace=True)


USING THE INTER-QUARTILE  RANGE METHOD TO DETECT OUTLIERS PRESENT IN NUMERICAL COLUMNS

USED IQR METHOD BECAUSE IN THE REAL-WORLD DATASET , MOST ARE SKEWED NOT NORMALLY DISTRIBUTED 

In [22]:
import numpy as np

num_df = df.select_dtypes(include=np.number)         # selects all numeric_types- int,float,complex
   
for i in num_df.columns :
    
    percen25 = df[i].quantile(0.25)   # first quartile
    percen75 = df[i].quantile(0.75)     # third quartile

    iqr = percen75 - percen25                # q3-q1   for lower&upperbound   

    lower_bound = percen25 - (1.5*iqr)       
    upper_bound = percen75 + (1.5*iqr)

    total = ( (df[i] < lower_bound) | (df[i] > upper_bound ) ).sum()

    if total > 0 :
        cleaned_list.append(f"{i} has total {total} potential outliers. No automatic action taken")
    
    
for i in cleaned_list :
    print(i)

SUCCESS: Split 'Ticket' into prefix/number and dropped original.
SUCCESS: Split 'Cabin' into prefix/number and dropped original.
Missing values of Age  has been imputed with value 28.0 
The Cabin_number is been dropped due to > 60% missing_values
PassengerId has 100% Unique values
Name has 100% Unique values
SibSp has 68.23793490460157% zeros 
Parch has 76.0942760942761% zeros 
Fare has 1.6835016835016834% zeros 
Age has total 66 potential outliers. No automatic action taken
SibSp has total 46 potential outliers. No automatic action taken
Parch has total 213 potential outliers. No automatic action taken
Fare has total 116 potential outliers. No automatic action taken
Ticket_number has total 44 potential outliers. No automatic action taken


In [26]:
high_cooreln 


{'Cabin_prefix',
 'Fare',
 'Pclass',
 'Sex',
 'SibSp',
 'Survived',
 'Ticket_number',
 'Ticket_prefix'}

In [23]:
df_copy

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    male  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                               Heikkinen, Miss. Laina  female  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                             Allen, Mr. William Henry    male  35.0      0   
..                                                 ...     ...   ...    ...   
886                              Montvila, Rev. Juozas    male  27.0      0   
887                       Graham, Miss. Margaret Edith  female  19.0      0   
888           Johnston, Miss. Catherine Helen "Carrie"  female   NaN      1   
889                              Behr, Mr. Karl Howell    male  26.0      0   
890                                Dooley, Mr. Patrick    male  32.0      0   

     Parch            Ticket     Fare Cabin Embarked  
0        0         A/5 21171   7.2500   NaN        S  
1        0          PC 17599  71.2833   C85        C  
2        0  STON/O2. 3101282   7.9250   NaN        S  
3        0            113803  53.1000  C123        S  
4        0            373450   8.0500   NaN        S  
..     ...               ...      ...   ...      ...  
886      0            211536  13.0000   NaN        S  
887      0            112053  30.0000   B42        S  
888      2        W./C. 6607  23.4500   NaN        S  
889      0            111369  30.0000  C148        C  
890      0            370376   7.7500   NaN        Q  

[891 rows x 12 columns]

In [24]:
df

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    male  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                               Heikkinen, Miss. Laina  female  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                             Allen, Mr. William Henry    male  35.0      0   
..                                                 ...     ...   ...    ...   
886                              Montvila, Rev. Juozas    male  27.0      0   
887                       Graham, Miss. Margaret Edith  female  19.0      0   
888           Johnston, Miss. Catherine Helen "Carrie"  female  28.0      1   
889                              Behr, Mr. Karl Howell    male  26.0      0   
890                                Dooley, Mr. Patrick    male  32.0      0   

     Parch     Fare Embarked Ticket_prefix  Ticket_number Cabin_prefix  
0        0   7.2500        S           A/5        21171.0          nan  
1        0  71.2833        C            PC        17599.0            C  
2        0   7.9250        S      STON/O2.      3101282.0          nan  
3        0  53.1000        S          NONE       113803.0            C  
4        0   8.0500        S          NONE       373450.0          nan  
..     ...      ...      ...           ...            ...          ...  
886      0  13.0000        S          NONE       211536.0          nan  
887      0  30.0000        S          NONE       112053.0            B  
888      2  23.4500        S         W./C.         6607.0          nan  
889      0  30.0000        C          NONE       111369.0            C  
890      0   7.7500        Q          NONE       370376.0          nan  

[891 rows x 13 columns]